In [1]:
import pandas as pd
import numpy as np

In [2]:
messages = pd.read_csv("data\messages.csv")
messages.head()

id                                            message  \
0   2  Weather update - a cold front from Cuba that c...   
1   7            Is the Hurricane over or is it not over   
2   8                    Looking for someone but no name   
3   9  UN reports Leogane 80-90 destroyed. Only Hospi...   
4  12  says: west side of Haiti, rest of the country ...   

                                            original   genre  
0  Un front froid se retrouve sur Cuba ce matin. ...  direct  
1                 Cyclone nan fini osinon li pa fini  direct  
2  Patnm, di Maryani relem pou li banm nouvel li ...  direct  
3  UN reports Leogane 80-90 destroyed. Only Hospi...  direct  
4  facade ouest d Haiti et le reste du pays aujou...  direct

In [3]:
categories = pd.read_csv("data\categories.csv")
categories.head()

id                                         categories
0   2  related-1;request-0;offer-0;aid_related-0;medi...
1   7  related-1;request-0;offer-0;aid_related-1;medi...
2   8  related-1;request-0;offer-0;aid_related-0;medi...
3   9  related-1;request-1;offer-0;aid_related-1;medi...
4  12  related-1;request-0;offer-0;aid_related-0;medi...

In [7]:
twitter = pd.read_csv("data\Twitter-sentiment-self-drive-DFE.csv")
twitter.head()

Unnamed: 0   _unit_id  _golden _unit_state  _trusted_judgments  \
0           0  724227031     True      golden                 236   
1           1  724227032     True      golden                 231   
2           2  724227033     True      golden                 233   
3           3  724227034     True      golden                 240   
4           4  724227035     True      golden                 240   

  _last_judgment_at sentiment  sentiment:confidence  our_id sentiment_gold  \
0               NaN         5                0.7579   10001           5\n4   
1               NaN         5                0.8775   10002           5\n4   
2               NaN         2                0.6805   10003           2\n1   
3               NaN         2                0.8820   10004           2\n1   
4               NaN         3                1.0000   10005              3   

                               sentiment_gold_reason  \
0  Author is excited about the development of the...   
1  Author is excited that driverless cars will be...   
2  The author is skeptical of the safety and reli...   
3    The author is skeptical of the project's value.   
4  Author is making an observation without expres...   

                                                text  
0  Two places I'd invest all my money if I could:...  
1  Awesome! Google driverless cars will help the ...  
2  If Google maps can't keep up with road constru...  
3  Autonomous cars seem way overhyped given the t...  
4  Just saw Google self-driving car on I-34. It w...

In [4]:
df_merged = messages.merge(categories, on="id")

In [5]:
df_merged()

TypeError: 'DataFrame' object is not callable

In [5]:
#This is a multi-label, multi-class problem
#The below was the suggested way, to create one hot encodings for the classes
#Function to return categories columns as new dataframe
import re
def categorize(series):
    columns = []
    for col in series.iloc[0].split(";"):
        columns.append(col.split("-")[0])
    arr = series.apply(lambda x: re.sub(r'\w+_*\w+-', '', x).split(";")).values
    
    return pd.DataFrame(list(arr), columns = columns).applymap(lambda x: int(x))
        

df_all = pd.concat([df_merged, categorize(df_merged["categories"])], axis=1).drop(columns=["categories","original"])


In [18]:
df_merged.categories = df_merged.categories.apply(categorize)
df_merged.categories.value_counts()

related    20042
Name: categories, dtype: int64

In [22]:
a = pd.Series([[1,2],[3,4]])
pd.DataFrame(list(a.values))

0  1
0  1  2
1  3  4

In [23]:
import re
re.sub(r'\w+_*\w+-', '', "aid_related-1")

'1'

In [26]:
a = np.array(["1","2"])
a.astype(int)

array([1, 2])

In [61]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.multioutput import MultiOutputClassifier
from sklearn.datasets import make_multilabel_classification
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix

X, y = make_multilabel_classification(n_samples=1000, n_classes=10)
clf = MultiOutputClassifier(RandomForestClassifier())
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2)
y_pred = clf.fit(X_train,y_train).predict(X_test)

from sklearn.metrics import r2_score

print(r2_score(y_test, y_pred))

-0.07214541208996342


C:\Users\vuanh\Anaconda3\lib\site-packages\sklearn\ensemble\forest.py:245: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
C:\Users\vuanh\Anaconda3\lib\site-packages\sklearn\ensemble\forest.py:245: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
C:\Users\vuanh\Anaconda3\lib\site-packages\sklearn\ensemble\forest.py:245: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
C:\Users\vuanh\Anaconda3\lib\site-packages\sklearn\ensemble\forest.py:245: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
C:\Users\vuanh\Anaconda3\lib\site-packages\sklearn\ensemble\forest.py:245: F

In [90]:
import sqlalchemy
from sqlalchemy import create_engine, text

engine = create_engine("sqlite+pysqlite:///data/DisasterResponse.db")
df_all.to_sql("test", con=engine, if_exists="replace")
with engine.connect() as conn:
    result = conn.execute(text("select message from test"))
    print(result.fetchall()[:3])



[('Weather update - a cold front from Cuba that could pass over Haiti',), ('Is the Hurricane over or is it not over',), ('Looking for someone but no name',)]


In [7]:
df_all.drop_duplicates(subset="message", inplace=True)

In [8]:
import nltk
nltk.download(["wordnet","punkt","stopwords"])

[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\vuanh\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\vuanh\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\vuanh\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [98]:
with engine.connect() as conn:
    df_new = pd.read_sql("test", con=conn)
for val in df_new.message.values:
    print(val)

Weather update - a cold front from Cuba that could pass over Haiti
Is the Hurricane over or is it not over
Looking for someone but no name
UN reports Leogane 80-90 destroyed. Only Hospital St. Croix functioning. Needs supplies desperately.
says: west side of Haiti, rest of the country today and tonight
Information about the National Palace-
Storm at sacred heart of jesus
Please, we need tents and water. We are in Silo, Thank you!
I would like to receive the messages, thank you
I am in Croix-des-Bouquets. We have health issues. They ( workers ) are in Santo 15. ( an area in Croix-des-Bouquets )
There's nothing to eat and water, we starving and thirsty.
I am in Petionville. I need more information regarding 4636
I am in Thomassin number 32, in the area named Pyron. I would like to have some water. Thank God we are fine, but we desperately need water. Thanks
Let's do it together, need food in Delma 75, in didine area
More information on the 4636 number in order for me to participate. ( To

In [99]:
df_all.columns

Index(['id', 'message', 'genre', 'related', 'request', 'offer', 'aid_related',
       'medical_help', 'medical_products', 'search_and_rescue', 'security',
       'military', 'child_alone', 'water', 'food', 'shelter', 'clothing',
       'money', 'missing_people', 'refugees', 'death', 'other_aid',
       'infrastructure_related', 'transport', 'buildings', 'electricity',
       'tools', 'hospitals', 'shops', 'aid_centers', 'other_infrastructure',
       'weather_related', 'floods', 'storm', 'fire', 'earthquake', 'cold',
       'other_weather', 'direct_report'],
      dtype='object')

In [6]:
import nltk
nltk.download(["wordnet", "punkt", "stopwords", "averaged_perceptron_tagger"])
from nltk.corpus import stopwords
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.tokenize import word_tokenize

from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.ensemble import RandomForestClassifier
from sklearn.multioutput import MultiOutputClassifier
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.metrics import confusion_matrix
from sklearn.pipeline import Pipeline, FeatureUnion

[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\vuanh\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\vuanh\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\vuanh\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\vuanh\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


In [7]:
def tokenize(text):
        tokens = word_tokenize(text)
        lemmatizer = WordNetLemmatizer()

        clean_tokens = []
        for tok in tokens:
            cleaned = lemmatizer.lemmatize(tok.strip().lower())
            clean_tokens.append(cleaned)
        
        clean_tokens = [w for w in clean_tokens if w not in stopwords.words("english")]
        
        return clean_tokens
# print(x.toarray())
class StartingVerbExtractor(BaseEstimator, TransformerMixin):

    def starting_verb(self, text):
        pos_tags = nltk.pos_tag(tokenize(text))
        first_word, first_tag = pos_tags[0]
        if first_tag in ['VB', 'VBP'] or first_word == 'RT':
            return True
        return False

    def fit(self, x, y=None):
        return self

    def transform(self, X):
        X_tagged = pd.Series(X).apply(self.starting_verb)
        return pd.DataFrame(X_tagged)


In [9]:
pipeline = Pipeline([
                    ("features", 
                        FeatureUnion([
                            ("text_pipeline", 
                                Pipeline([
                                    ("vect", CountVectorizer(tokenizer = tokenize)),
                                    ("tfidf", TfidfTransformer())
                                ])
                            ),
                            ("verb_extract", StartingVerbExtractor())
                        ])
                    ),
                    ("clf", MultiOutputClassifier(estimator=RandomForestClassifier(), n_jobs=2))
                    ])

X = df_all.message 
y = df_all.iloc[:,3:]


In [10]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)

In [12]:
def starting_verb(text):
    pos_tags = nltk.pos_tag(tokenize(text))
    first_word, first_tag = pos_tags[0]
    if first_tag in ['VB', 'VBP'] or first_word == 'RT':
        return True
    return False


# for ind, val in enumerate(X_train.values):
#     try:
#         starting_verb(val)
#     except:
#         print(ind, val)
X_train.iloc[15868]

'                           '

In [22]:
# pipeline.fit(X, y.iloc[:100,:])
pipeline.fit(X_train, y_train)
# y_pred_100 = pipeline.predict(X[101:201])
# y_pred_100

IndexError: list index out of range

In [43]:
from sklearn.metrics import r2_score

r2_score(y.iloc[101:201,:], y_pred_100)

0.12547826512134444

In [44]:
y_pred_100.shape

(100, 36)

In [45]:
y.iloc[101:201,:].shape

(100, 36)

In [47]:
from sklearn.preprocessing import OneHotEncoder

encoder = OneHotEncoder()

encoded_type = encoder.fit_transform(df_all.genre.values.reshape(-1,1))
encoder.categories_

[array(['direct', 'news', 'social'], dtype=object)]

In [54]:
df_all_new = pd.concat([df_all, pd.DataFrame(encoded_type.toarray(), columns=encoder.categories_)], axis=1).drop(columns=["genre"])
df_all_new.head()

id                                            message  related  request  \
0   2.0  Weather update - a cold front from Cuba that c...      1.0      0.0   
1   7.0            Is the Hurricane over or is it not over      1.0      0.0   
2   8.0                    Looking for someone but no name      1.0      0.0   
3   9.0  UN reports Leogane 80-90 destroyed. Only Hospi...      1.0      1.0   
4  12.0  says: west side of Haiti, rest of the country ...      1.0      0.0   

   offer  aid_related  medical_help  medical_products  search_and_rescue  \
0    0.0          0.0           0.0               0.0                0.0   
1    0.0          1.0           0.0               0.0                0.0   
2    0.0          0.0           0.0               0.0                0.0   
3    0.0          1.0           0.0               1.0                0.0   
4    0.0          0.0           0.0               0.0                0.0   

   security  ...  floods  storm  fire  earthquake  cold  other_weather  \
0       0.0  ...     0.0    0.0   0.0         0.0   0.0            0.0   
1       0.0  ...     0.0    1.0   0.0         0.0   0.0            0.0   
2       0.0  ...     0.0    0.0   0.0         0.0   0.0            0.0   
3       0.0  ...     0.0    0.0   0.0         0.0   0.0            0.0   
4       0.0  ...     0.0    0.0   0.0         0.0   0.0            0.0   

   direct_report  (direct,)  (news,)  (social,)  
0            0.0        1.0      0.0        0.0  
1            0.0        1.0      0.0        0.0  
2            0.0        1.0      0.0        0.0  
3            0.0        1.0      0.0        0.0  
4            0.0        1.0      0.0        0.0  

[5 rows x 41 columns]

In [52]:
pd.DataFrame(encoded_type.toarray(), columns=encoder.categories_)

direct news social
0        1.0  0.0    0.0
1        1.0  0.0    0.0
2        1.0  0.0    0.0
3        1.0  0.0    0.0
4        1.0  0.0    0.0
...      ...  ...    ...
26172    0.0  1.0    0.0
26173    0.0  1.0    0.0
26174    0.0  1.0    0.0
26175    0.0  1.0    0.0
26176    0.0  1.0    0.0

[26177 rows x 3 columns]

In [18]:
from sqlalchemy import create_engine
import sys
import pandas as pd
import numpy as np

import nltk
nltk.download(["wordnet", "punkt", "stopwords"])
from nltk.corpus import stopwords
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.tokenize import word_tokenize

from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.ensemble import RandomForestClassifier
from sklearn.multioutput import MultiOutputClassifier
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.metrics import r2_score
from sklearn.pipeline import Pipeline, FeatureUnion



def main():
    
    #STEP 1: Load data from DB
    # if len(sys.argv) >1:
    #     db_name = sys.argv[1]
    # else:
    db_name = "data\DisasterResponse.db"
    db_url = "".join(["sqlite+pysqlite:///", db_name])
    engine = create_engine(db_url)
    with engine.connect() as conn:
        df = pd.read_sql("disres", con=conn)
    
    #STEP 2: Processing text
    #Function for tokenizing text
    def tokenize(text):
        tokens = word_tokenize(text)
        lemmatizer = WordNetLemmatizer()

        clean_tokens = []
        for tok in tokens:
            cleaned = lemmatizer.lemmatize(tok.strip().lower())
            clean_tokens.append(cleaned)
        
        clean_tokens = [w for w in clean_tokens if w not in stopwords.words("english")]
        
        return clean_tokens
    
    #Custom estimator class to identify if 1st word of response is a verb
    class StartingVerbExtractor(BaseEstimator, TransformerMixin):

        def starting_verb(self, text):
            pos_tags = nltk.pos_tag(tokenize(text))
            first_word, first_tag = pos_tags[0]
            if first_tag in ['VB', 'VBP'] or first_word == 'RT':
                return True
            return False

        def fit(self, x, y=None):
            return self

        def transform(self, X):
            X_tagged = pd.Series(X).apply(self.starting_verb).values
            return pd.DataFrame(X_tagged)
    
    #STEP 3: Create Pipeline
    pipeline = Pipeline([
                ("features", 
                    FeatureUnion([
                        ("text_pipeline", 
                            Pipeline([
                                ("vect", CountVectorizer(tokenizer = tokenize)),
                                ("tfidf", TfidfTransformer())
                            ])
                        ),
                        ("verb_extract", StartingVerbExtractor())
                    ])
                ),
                ("clf", MultiOutputClassifier(estimator=RandomForestClassifier(), n_jobs=2))
                ])

    X = df["message"]
    y = df.iloc[:,4:]

    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)
    pipeline.fit(X_train, y_train)

main()

[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\vuanh\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\vuanh\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\vuanh\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


IndexError: list index out of range